In [1]:
using Random

include("SimpleAgentEvents/src/SimpleAgentEvents.jl")

using .SimpleAgentEvents
using .SimpleAgentEvents.Scheduler

In [2]:
@enum Status susceptible infected immune dead

mutable struct Person
    status :: Status
    contacts :: Vector{Person}
    x :: Float64
    y :: Float64
end

Person(x, y) = Person(susceptible, [], x, y)
Person(state, x, y) = Person(state, [], x, y)

Person

In [3]:
mutable struct Simulation
    scheduler :: PQScheduler{Float64}
    inf :: Float64
    rec :: Float64
    imm :: Float64
    mort :: Float64
    
    pop :: Vector{Person}
end

scheduler(sim :: Simulation) = sim.scheduler

Simulation(i, r, u, m) = Simulation(PQScheduler{Float64}(), i, r, u, m, [])

Simulation

In [4]:
@processes SIR sim person::Person begin
    @poisson(sim.inf * count(p -> p.status == infected, person.contacts)) ~
        person.status == susceptible        => 
            begin
                person.status = infected
                [person; person.contacts]
            end

    @poisson(sim.rec)  ~
        person.status == infected           => 
            begin
                person.status = susceptible
                [person; person.contacts]
            end

    @poisson(sim.imm)  ~
        person.status == infected           => 
            begin
                person.status = immune
                person.contacts
            end
end


spawn_SIR (generic function with 1 method)

In [5]:
include("setup_world.jl")
include("draw.jl")

draw_sim (generic function with 3 methods)

In [6]:
sim = Simulation(0.5, 0.1, 0.2, 0)
sim.pop = setup_grid(50, 50)
sim.pop[1].status = infected


for person in sim.pop
    spawn_SIR(person, sim)
end

Random.seed!(42);

In [7]:
for t in  1:10
    upto!(sim.scheduler, time_now(sim.scheduler) + 1.0)
    println(time_now(sim.scheduler), ", ", 
        count(p -> p.status == infected, sim.pop), ", ",
        count(p -> p.status == susceptible, sim.pop))
end

1.0, 0, 2499
2.0, 3, 2496
3.0, 4, 2494
4.0, 8, 2488
5.0, 14, 2480
6.0, 22, 2468
7.0, 17, 2464
8.0, 21, 2459
9.0, 32, 2447
10.0, 41, 2431


In [8]:
draw_sim(sim)

In [9]:
@processes SIRm sim person::Person begin
    @poisson(sim.inf * count(p -> p.status == infected, person.contacts)) ~
        person.status == susceptible        => 
            begin
                person.status = infected
                [person; person.contacts]
            end

    @poisson(sim.rec)  ~
        person.status == infected           => 
            begin
                person.status = susceptible
                [person; person.contacts]
            end

    @poisson(sim.imm)  ~
        person.status == infected           => 
            begin
                person.status = immune
                person.contacts
            end
    
    @poisson(sim.mort)  ~
        person.status == infected           => 
            begin
                person.status = dead
                person.contacts
            end    
end


spawn_SIRm (generic function with 1 method)

In [10]:
sim_m = Simulation(0.5, 0.1, 0.2, 0.1)
sim_m.pop = setup_grid(50, 50)
sim_m.pop[1].status = infected


for person in sim_m.pop
    spawn_SIRm(person, sim_m)
end

Random.seed!(42);

In [11]:
for t in  1:10
    upto!(sim_m.scheduler, time_now(sim_m.scheduler) + 1.0)
    println(time_now(sim_m.scheduler), ", ", 
        count(p -> p.status == infected, sim_m.pop), ", ",
        count(p -> p.status == susceptible, sim_m.pop))
end


1.0, 3, 2497
2.0, 2, 2497
3.0, 4, 2493
4.0, 10, 2483
5.0, 11, 2477
6.0, 16, 2469
7.0, 19, 2460
8.0, 23, 2451
9.0, 28, 2441
10.0, 38, 2426


In [12]:
draw_sim(sim_m)

In [24]:
sim_m2 = Simulation(0.5, 0.1, 0.2, 0.1)
sim_m2.pop = setup_geograph(2500, 0.03, 100)
sim_m2.pop[1].status = infected

for person in sim_m2.pop
    spawn_SIRm(person, sim_m2)
end

Random.seed!(42);

In [25]:
for t in  1:10
    upto!(sim_m2.scheduler, time_now(sim_m2.scheduler) + 1.0)
    println(time_now(sim_m2.scheduler), ", ", 
        count(p -> p.status == infected, sim_m.pop), ", ",
        count(p -> p.status == susceptible, sim_m.pop))
end


1.0, 38, 2426
2.0, 38, 2426
3.0, 38, 2426
4.0, 38, 2426
5.0, 38, 2426
6.0, 38, 2426
7.0, 38, 2426
8.0, 38, 2426
9.0, 38, 2426
10.0, 38, 2426


In [26]:
draw_sim(sim_m2)